# 1. `Customer_Running_Count_Query.sql`

## Proposition
This query calculates the running count of customers per territory, ordered by the modification date of each customer, and then finds the maximum running count per territory. Finally, it retrieves the top 5 territories with the highest running customer count.

## Tables Involved
- `Sales.Customer`: Contains customer information, including `CustomerID`, `TerritoryID`, and `ModifiedDate`.
- `Person.Person`: Contains personal details, including `FirstName`, `LastName`, and `BusinessEntityID`.

### Further Details
- The `CustomerRunningCount` CTE (Common Table Expression) calculates a running count of customers (`RunningCustomerCount`) by territory (`TerritoryID`), using a window function.
- The `MaxRunningCustomerCountPerTerritory` CTE finds the maximum value of the running customer count for each territory.
- The final query retrieves the top 5 territories with the highest `MaxRunningCustomerCount` and orders the results in descending order.

In [22]:
USE	[AdventureWorks2019]
GO

WITH	CustomerRunningCount	AS	(
    SELECT
        c.CustomerID,
        c.TerritoryID,
        p.FirstName,
        p.LastName,
        c.ModifiedDate,
        COUNT(c.CustomerID) OVER	(
            PARTITION	BY	c.TerritoryID
				ORDER	BY	c.ModifiedDate
            ROWS	BETWEEN UNBOUNDED	PRECEDING	AND CURRENT ROW
        )	AS	RunningCustomerCount
    FROM
        Sales.Customer	AS	c
    LEFT	JOIN
        Person.Person	AS	p
			ON	c.PersonID	=	p.BusinessEntityID
),
MaxRunningCustomerCountPerTerritory	AS	(
    SELECT
        TerritoryID,
        MAX(RunningCustomerCount)	AS	MaxRunningCustomerCount
    FROM
        CustomerRunningCount
    GROUP	BY
        TerritoryID
)
SELECT	TOP 5
    TerritoryID,
    MaxRunningCustomerCount
FROM
    MaxRunningCustomerCountPerTerritory
ORDER	BY
    MaxRunningCustomerCount DESC;


Commands completed successfully.

(5 rows affected)

Total execution time: 00:00:00.022

TerritoryID MaxRunningCustomerCount 4 4696 9 3665 1 3520 10 1991 7 1884

___
___
___

# 2. `Top_Sales_Persons_Summary.sql`

## Proposition
This query retrieves the top five salespersons based on the total sales amount they generated. It calculates the total sales amount for each salesperson and ranks them in descending order of sales. The query also includes bonus and year-to-date (YTD) sales information for each salesperson.

## Tables Involved
- `Sales.SalesPerson`: Stores information about salespersons, including `BusinessEntityID`, `Bonus`, and `SalesYTD`.
- `Sales.SalesOrderHeader`: Stores sales order information, including `SalesOrderID`, `TotalDue`, and `SalesPersonID`.

### Further Details
- The `SalesSummary` common table expression (CTE) calculates the total sales amount for each salesperson by grouping sales orders.
- The `RankedSalesSummary` CTE ranks the salespersons based on their total sales amount in descending order.
- The main query selects the top five salespersons, including their `SalesPersonID`, `Bonus`, `SalesYTD`, `TotalSalesAmount`, and rank.

In [23]:
USE	[AdventureWorks2019]
GO

WITH	SalesSummary	AS	(
	SELECT
        sp.BusinessEntityID	AS	SalesPersonID,
        sp.Bonus,
        sp.SalesYTD,
        SUM(soh.TotalDue)	AS	TotalSalesAmount
	FROM
		Sales.SalesPerson		sp
		JOIN
		Sales.SalesOrderHeader	soh
		ON	sp.BusinessEntityID	=	soh.SalesPersonID
	GROUP	BY
		sp.BusinessEntityID,	sp.Bonus,	sp.SalesYTD
),
RankedSalesSummary	AS	(
	SELECT
		SalesPersonID,
		Bonus,
		SalesYTD,
		TotalSalesAmount,
		RANK()	OVER	(
			ORDER	BY
				TotalSalesAmount	DESC
		)	                AS	SalesRank
	FROM	SalesSummary
)

SELECT 
    SalesPersonID,
    Bonus,
    SalesYTD,
    TotalSalesAmount,
    SalesRank
FROM
	RankedSalesSummary
WHERE
	SalesRank	<=	5;
GO

Commands completed successfully.

(5 rows affected)

Total execution time: 00:00:00.015

SalesPersonID Bonus SalesYTD TotalSalesAmount SalesRank 276 2000.00 4251368.5497 11695019.0605 1 277 2500.00 3189418.3662 11342385.8968 2 275 4100.00 3763178.1787 10475367.0751 3 289 5150.00 4116871.2277 9585124.9477 4 279 6700.00 2315185.611 8086073.6761 5

___
___
___

# 3. `Top_Customer_Store_Purchases.sql`

## Proposition
This query retrieves information about the top purchases made by customers at stores in the AdventureWorks2019 database. It ranks each customer's sales orders based on the total amount due and returns only the highest-ranked order for each customer.

## Tables Involved
- `Sales.Customer`: Stores customer information, including `CustomerID`, `PersonID`, and `StoreID`.
- `Person.Person`: Stores personal information about individuals, such as `FirstName` and `LastName`.
- `Sales.Store`: Stores store information, including `BusinessEntityID` and `Name`.
- `Sales.SalesOrderHeader`: Stores sales order information, including `SalesOrderID`, `TotalDue`, and `OrderDate`.

### Further Details
- The `SalesWithRank` common table expression (CTE) calculates the rank of each sales order for every customer based on the `TotalDue` amount.
- The main query selects only the highest-ranked (`SalesRank = 1`) sales order for each customer, sorted by `TotalDue` in descending order.

In [24]:
USE [AdventureWorks2019]
GO

WITH
	SalesWithRank	AS	(
    SELECT
        p.FirstName	+	' '	+	p.LastName	AS	CustomerName,
        soh.SalesOrderID,
        soh.OrderDate,
        soh.TotalDue,
        s.BusinessEntityID	AS	StoreID,
        s.Name	AS	StoreName,
        RANK()	OVER	(
		PARTITION	BY	p.BusinessEntityID
			ORDER	BY	soh.TotalDue	DESC
		)	AS	SalesRank
    FROM
		Sales.Customer			c
    JOIN
		Person.Person			p
			ON	c.PersonID		=	p.BusinessEntityID
    JOIN
		Sales.Store				s
			ON	c.StoreID		=	s.BusinessEntityID
    JOIN
		Sales.SalesOrderHeader	soh
			ON	c.CustomerID	=	soh.CustomerID
)

SELECT
    CustomerName,
    SalesOrderID,
    StoreName,
    TotalDue,
    SalesRank
FROM
    SalesWithRank
WHERE
    SalesRank   =   1
ORDER   BY
    TotalDue    DESC;
GO

Commands completed successfully.

(643 rows affected)

Total execution time: 00:00:00.021

CustomerName SalesOrderID StoreName TotalDue SalesRank Raul Casts 51131 Westside Plaza 187487.825 1 Ryan Calafato 46616 Retail Mall 170512.6689 1 Mandy Vance 46981 Metropolitan Equipment 166537.0808 1 Kirk DeGrasse 47395 Outdoor Equipment Store 165028.7482 1 Jane McCarty 47369 Bicycle Merchandise Warehouse 158056.5449 1 Kevin Liu 47355 Eastside Department Store 145741.8553 1 Anton Kirilov 51822 Field Trip Store 145454.366 1 Joseph Cantoni 44518 Tread Industries 142312.2199 1 Robertson Lee 51858 Perfect Toys 140042.1209 1 Edward Kozlowski 57150 Roadway Bicycle Supply 137721.3102 1 Robin McGuigan 46607 Health Spa, Limited 135606.6769 1 Stacey Cereghino 46660 Fitness Toy Store 132727.8506 1 Phyllis Huntsman 43884 Hardware Components 130416.4829 1 Krishna Sunkammurali 53573 Metropolitan Bicycle Supply 130249.2557 1 Andrew Dixon 47455 Excellent Riding Supplies 126992.2202 1 Lindsey Camacho 51830 Thorough Parts and Repair Services 126852.1615 1 Steven Brown 47441 Golf and Cycle Store 126830.9608 1 Holly Dickson 51739 Registered Cycle Store 125157.3774 1 Frank Mart¡nez 51126 Rally Master Company Inc 124397.7924 1 Roger Harui 57105 Brakes and Gears 124249.4919 1 Scott Culp 46643 Friendly Bike Shop 123497.0664 1 Ranjit Varkey Chudukatil 44528 Great Bicycle Supply 122500.6617 1 Blaine Dockter 47018 Farthermost Bike Shop 121122.2311 1 Elizabeth Sullivan 53621 Extraordinary Bike Works 120512.2708 1 Barbara Calone 50289 Sheet Metal Manufacturing 118581.3375 1 Ryan Danner 55254 Best Cycle Store 117506.1173 1 Helen Dennis 47416 Sales and Supply Company 116463.9102 1 Patricia Vasquez 50297 Mail-Order Outlet 116390.7349 1 Michael Graff 47400 Commercial Sporting Goods 116295.0969 1 Stacie Mcanich 51761 Global Bike Retailers 115124.6277 1 Lola McCarthy 51711 Closeout Boutique 114536.7764 1 James McCoy 46645 Leather Seat Factory 114197.9702 1 Robert Vessa 47990 Totes & Baskets Company 112859.9318 1 Mari Caldwell 51823 Metro Metals Co. 112685.2793 1 Janet Gates 47658 Modular Cycle Systems 112076.4746 1 Teresa Atkinson 44777 Extended Bike Sales 112067.3649 1 Valerie Hendricks 46629 First Bike Store 111633.3826 1 Carlton Carlisle 53535 Camping and Sports Store 111328.3281 1 Marcia Sultan 51160 Top Sports Supply 111207.2228 1 Phyllis Allen 44552 eCommerce Bikes 110276.574 1 Margaret Vanderkamp 51721 Permanent Finish Products 109948.7407 1 Yuping Tian 50204 Tenth Bike Store 109900.1475 1 Reuben D'sa 45529 Vigorous Exercise Company 109340.8212 1 Dave Browning 49888 Eastside Sporting Goods 108780.5231 1 Joseph Castellucio 47366 Corner Bicycle Supply 108757.3001 1 Terry Eminhizer 53458 Action Bicycle Specialists 105420.9481 1 Mary Billstrom 57054 Favorite Toy Distributor 105120.5963 1 Mitch Kennedy 50304 Reasonable Bicycle Sales 104751.3605 1 Conor Cunningham 44762 Fashionable Bikes and Accessories 104545.315 1 Jon Grande 53472 Riding Cycles 103883.1767 1 François Ferrier 67297 Great Bikes 103227.0017 1 Nate Sun 53497 Racing Sales and Service 101657.3019 1 Robert Bernacchi 53518 Safe Cycles Shop 99023.6736 1 Richard Bready 44284 Latest Sports Equipment 98932.197 1 Brenda Diaz 44788 Downtown Hotel 97765.7518 1 Maxwell Amland 44534 Serious Cycles 96937.2022 1 Kathleen Garza 71841 Rural Cycle Emporium 93791.205 1 J. Phillip Alexander 44761 Global Plaza 92470.0936 1 Christopher Beck 53562 Bulk Discount Store 91734.9579 1 Baris Cetinok 49843 Casual Bicycle Store 90675.5705 1 Stefan Delmarco 46988 Preferred Bikes 89930.0449 1 Frances Adams 51121 Area Bike Accessories 89678.1892 1 John Evans 51090 Real Sporting Goods 87003.1753 1 John Arthur 46094 The Gear Store 84134.3764 1 Margaret Krupka 44523 Outdoor Sports Supply 83772.7786 1 John Kelly 46089 Sturdy Toys 82830.5278 1 Eugene Kogan 51745 Mountain Bike Center 82706.5451 1 James Hendergart 45061 Better Bike Shop 82490.9371 1 Bart Duncan 51826 Stock Parts and Supplies 81561.0362 1 Min Su 47377 Getaway Inn 81546.9865 1 Thierry D'Hers 46614 Citywide Service and Repair 81289.4617 1 Alexander Berger 58932 Odometers

___
___
___

# 4. `Top_Product_WorkOrders.sql`

## Proposition
This query retrieves information about the top work orders for each product in the AdventureWorks2019 database. It calculates the total order quantity and average order quantity for each product and ranks the work orders based on their start date, returning the top 5 work orders for each product.

## Tables Involved
- `Production.Product`: Stores product information, including `ProductID` and `Name`.
- `Production.WorkOrder`: Stores work order information, including `WorkOrderID`, `ProductID`, and `OrderQty`.

### Further Details
- The `ProductSalesSummary` common table expression (CTE) calculates the total and average order quantities for each product using window functions.
- The `OrderRank` is calculated for each product's work orders based on the `StartDate` in descending order.
- The main query selects the top 5 work orders for each product, sorted by `ProductName` and `OrderRank`.

In [25]:
USE [AdventureWorks2019]
GO

WITH	ProductSalesSummary	AS	(
    SELECT
        p.ProductID,
        p.[Name]			AS	ProductName,
        woh.WorkOrderID,
        woh.OrderQty,
        SUM(woh.OrderQty)	OVER	(
			PARTITION	BY	p.ProductID
		)	AS	TotalOrderQuantity,
        AVG(woh.OrderQty)	OVER	(
			PARTITION	BY	p.ProductID
		)	AS	AvgOrderQuantity,
        ROW_NUMBER()		OVER	(
			PARTITION	BY	p.ProductID
				ORDER	BY	woh.StartDate	DESC
		)	AS	OrderRank
    FROM
		Production.[Product]	p
    JOIN
		Production.WorkOrder	woh
			ON	p.ProductID	=	woh.ProductID
)

SELECT
    ProductName,
    WorkOrderID,
    OrderQty,
    TotalOrderQuantity,
    AvgOrderQuantity,
    OrderRank
FROM
	ProductSalesSummary
WHERE
	OrderRank	<=	5
ORDER	BY 
	ProductName,
	OrderRank;
GO

Commands completed successfully.

(1190 rows affected)

Total execution time: 00:00:00.083

ProductName WorkOrderID OrderQty TotalOrderQuantity AvgOrderQuantity OrderRank BB Ball Bearing 72571 260 911890 834 1 BB Ball Bearing 72482 400 911890 834 2 BB Ball Bearing 72366 470 911890 834 3 BB Ball Bearing 72256 370 911890 834 4 BB Ball Bearing 72149 400 911890 834 5 Blade 72588 52 236002 215 1 Blade 72499 80 236002 215 2 Blade 72383 94 236002 215 3 Blade 72273 74 236002 215 4 Blade 72166 80 236002 215 5 Chain Stays 72572 52 234734 214 1 Chain Stays 72483 80 234734 214 2 Chain Stays 72367 94 234734 214 3 Chain Stays 72257 74 234734 214 4 Chain Stays 72150 80 234734 214 5 Down Tube 72573 26 117367 107 1 Down Tube 72484 40 117367 107 2 Down Tube 72368 47 117367 107 3 Down Tube 72258 37 117367 107 4 Down Tube 72151 40 117367 107 5 Fork Crown 72590 26 118001 107 1 Fork Crown 72501 40 118001 107 2 Fork Crown 72385 47 118001 107 3 Fork Crown 72275 37 118001 107 4 Fork Crown 72168 40 118001 107 5 Fork End 72589 52 236002 215 1 Fork End 72500 80 236002 215 2 Fork End 72384 94 236002 215 3 Fork End 72274 74 236002 215 4 Fork End 72167 80 236002 215 5 Front Derailleur 72562 26 91081 82 1 Front Derailleur 72473 40 91081 82 2 Front Derailleur 72357 47 91081 82 3 Front Derailleur 72247 37 91081 82 4 Front Derailleur 72140 40 91081 82 5 Handlebar Tube 72577 26 94218 86 1 Handlebar Tube 72488 40 94218 86 2 Handlebar Tube 72372 47 94218 86 3 Handlebar Tube 72262 37 94218 86 4 Handlebar Tube 72155 40 94218 86 5 Head Tube 72578 26 117367 107 1 Head Tube 72489 40 117367 107 2 Head Tube 72373 47 117367 107 3 Head Tube 72263 37 117367 107 4 Head Tube 72156 40 117367 107 5 HL Bottom Bracket 72570 4 23085 21 1 HL Bottom Bracket 72481 5 23085 21 2 HL Bottom Bracket 72365 8 23085 21 3 HL Bottom Bracket 72255 9 23085 21 4 HL Bottom Bracket 72148 9 23085 21 5 HL Crankset 72567 2 14568 20 1 HL Crankset 72478 3 14568 20 2 HL Crankset 72362 5 14568 20 3 HL Crankset 72252 3 14568 20 4 HL Crankset 72145 7 14568 20 5 HL Fork 72587 19 48531 43 1 HL Fork 72498 17 48531 43 2 HL Fork 72382 22 48531 43 3 HL Fork 72272 15 48531 43 4 HL Fork 72165 20 48531 43 5 HL Headset 72538 2 14210 19 1 HL Headset 72436 3 14210 19 2 HL Headset 72324 5 14210 19 3 HL Headset 72213 3 14210 19 4 HL Headset 72107 7 14210 19 5 HL Hub 72580 44 128226 117 1 HL Hub 72491 58 128226 117 2 HL Hub 72375 78 128226 117 3 HL Hub 72265 48 128226 117 4 HL Hub 72158 60 128226 117 5 HL Mountain Frame - Black, 38 72534 2 4318 9 1 HL Mountain Frame - Black, 38 72433 2 4318 9 2 HL Mountain Frame - Black, 38 72103 1 4318 9 3 HL Mountain Frame - Black, 38 71892 4 4318 9 4 HL Mountain Frame - Black, 38 71795 1 4318 9 5 HL Mountain Frame - Black, 42 72533 3 4479 9 1 HL Mountain Frame - Black, 42 72431 1 4479 9 2 HL Mountain Frame - Black, 42 72319 1 4479 9 3 HL Mountain Frame - Black, 42 72209 2 4479 9 4 HL Mountain Frame - Black, 42 71994 3 4479 9 5 HL Mountain Frame - Black, 44 15597 1 695 10 1 HL Mountain Frame - Black, 44 15135 1 695 10 2 HL Mountain Frame - Black, 44 14821 1 695 10 3 HL Mountain Frame - Black, 44 14566 58 695 10 4 HL Mountain Frame - Black, 44 14502 3 695 10 5 HL Mountain Frame - Black, 46 72432 2 2111 5 1 HL Mountain Frame - Black, 46 72320 2 2111 5 2 HL Mountain Frame - Black, 46 72102 3 2111 5 3 HL Mountain Frame - Black, 46 71995 3 2111 5 4 HL Mountain Frame - Black, 46 71794 1 2111 5 5 HL Mountain Frame - Black, 48 15812 1 747 9 1 HL Mountain Frame - Black, 48 15734 1 747 9 2 HL Mountain Frame - Black, 48 15598 1 747 9 3 HL Mountain Frame - Black, 48 15448 1 747 9 4 HL Mountain Frame - Black, 48 15395 1 747 9 5 HL Mountain Frame - Silver, 38 72535 2 4242 8 1 HL Mountain Frame - Silver, 38 72321 5 4242 8 2 HL Mountain Frame - Silver, 38 72210 2 4242 8 3 HL Mountain Frame - Silver, 38 72104 1 4242 8 4 HL Mountain Frame - Silver, 38 71996 3 4242 8 5 HL Mountain Frame - Silver, 42 72531 3 3174 6 1 HL Mountain Frame - Silver, 42 72429 1 3174 6 2 HL Mountain Frame - Silver, 42 72317 4 3174 6 3 HL Mountain Frame - Silver, 42 72208 2 3174 6 4 HL Mountain Frame - Silver, 42 72101 5

___
___
___

# 5. `Employee_Work_Order_Summary.sql`

## Proposition
This query retrieves a summary of the work orders completed by each employee in the AdventureWorks2019 database. It calculates the total work duration for each employee and retrieves the most recent work order date. The query ranks the work orders for each employee, returning the top 3 most recent work orders.

## Tables Involved
- `HumanResources.Employee`: Stores employee information, including `BusinessEntityID`.
- `Person.Person`: Stores personal information about individuals, such as `FirstName` and `LastName`.
- `Production.WorkOrder`: Stores work order information, including `WorkOrderID`, `StartDate`, and `EndDate`.

### Further Details
- The `EmployeeWorkSummary` common table expression (CTE) calculates the total work duration and the most recent work order date for each employee using window functions.
- The `WorkOrderRank` is calculated for each employee's work orders based on the `StartDate` in descending order.
- The main query selects the top 3 work orders for each employee, sorted by `EmployeeName` and `WorkOrderRank`.

In [26]:
USE	[AdventureWorks2019]
GO

WITH	EmployeeWorkSummary	AS	(
    SELECT
        e.BusinessEntityID					AS	EmployeeID,
        p.FirstName	+	' '	+	p.LastName	AS	EmployeeName,
        woh.WorkOrderID,
        woh.StartDate,
        woh.EndDate,
        DATEDIFF	(day,	woh.StartDate,	woh.EndDate)
											AS	WorkDuration,
        SUM(DATEDIFF(day,	woh.StartDate,	woh.EndDate))	OVER	(
			PARTITION	BY	e.BusinessEntityID
		)									AS	TotalWorkDuration,
        MAX(woh.EndDate)									OVER	(
			PARTITION	BY	e.BusinessEntityID
		)									AS	LastWorkOrderDate,
        ROW_NUMBER()										OVER	(
			PARTITION	BY	e.BusinessEntityID
				ORDER	BY	woh.StartDate	DESC
		)									AS	WorkOrderRank
    FROM
		HumanResources.Employee	e
    JOIN
		Person.Person			p
			ON	e.BusinessEntityID	=	p.BusinessEntityID
    JOIN
		Production.WorkOrder	woh
			ON	e.BusinessEntityID	=	woh.ScrapReasonID
)

SELECT
    EmployeeName,
    WorkOrderID,
    StartDate,
    EndDate,
    WorkDuration,
    TotalWorkDuration,
    LastWorkOrderDate,
    WorkOrderRank
FROM
	EmployeeWorkSummary
WHERE
	WorkOrderRank	<=	3
ORDER	BY
	EmployeeName,	WorkOrderRank;
GO

Commands completed successfully.

(48 rows affected)

Total execution time: 00:00:00.019

EmployeeName WorkOrderID StartDate EndDate WorkDuration TotalWorkDuration LastWorkOrderDate WorkOrderRank David Bradley 71098 2014-05-19 00:00:00.000 2014-05-29 00:00:00.000 10 564 2014-05-29 00:00:00.000 1 David Bradley 69497 2014-05-04 00:00:00.000 2014-05-20 00:00:00.000 16 564 2014-05-29 00:00:00.000 2 David Bradley 67397 2014-04-15 00:00:00.000 2014-04-25 00:00:00.000 10 564 2014-05-29 00:00:00.000 3 Diane Margheim 72050 2014-05-28 00:00:00.000 2014-06-07 00:00:00.000 10 436 2014-06-07 00:00:00.000 1 Diane Margheim 71847 2014-05-26 00:00:00.000 2014-06-05 00:00:00.000 10 436 2014-06-07 00:00:00.000 2 Diane Margheim 70148 2014-05-10 00:00:00.000 2014-05-20 00:00:00.000 10 436 2014-06-07 00:00:00.000 3 Dylan Miller 68245 2014-04-23 00:00:00.000 2014-05-03 00:00:00.000 10 380 2014-05-03 00:00:00.000 1 Dylan Miller 66545 2014-04-07 00:00:00.000 2014-04-17 00:00:00.000 10 380 2014-05-03 00:00:00.000 2 Dylan Miller 66042 2014-04-03 00:00:00.000 2014-04-19 00:00:00.000 16 380 2014-05-03 00:00:00.000 3 Gail Erickson 71430 2014-05-22 00:00:00.000 2014-06-01 00:00:00.000 10 546 2014-06-01 00:00:00.000 1 Gail Erickson 71328 2014-05-21 00:00:00.000 2014-05-31 00:00:00.000 10 546 2014-06-01 00:00:00.000 2 Gail Erickson 70132 2014-05-10 00:00:00.000 2014-05-20 00:00:00.000 10 546 2014-06-01 00:00:00.000 3 Gigi Matthew 72256 2014-05-30 00:00:00.000 2014-06-09 00:00:00.000 10 524 2014-06-09 00:00:00.000 1 Gigi Matthew 71853 2014-05-26 00:00:00.000 2014-06-05 00:00:00.000 10 524 2014-06-09 00:00:00.000 2 Gigi Matthew 71655 2014-05-24 00:00:00.000 2014-06-03 00:00:00.000 10 524 2014-06-09 00:00:00.000 3 Janice Galvin 72377 2014-05-31 00:00:00.000 2014-06-10 00:00:00.000 10 732 2014-06-10 00:00:00.000 1 Janice Galvin 69276 2014-05-03 00:00:00.000 2014-05-13 00:00:00.000 10 732 2014-06-10 00:00:00.000 2 Janice Galvin 66678 2014-04-08 00:00:00.000 2014-04-18 00:00:00.000 10 732 2014-06-10 00:00:00.000 3 Jossef Goldberg 71836 2014-05-26 00:00:00.000 2014-06-05 00:00:00.000 10 530 2014-06-05 00:00:00.000 1 Jossef Goldberg 71438 2014-05-22 00:00:00.000 2014-06-01 00:00:00.000 10 530 2014-06-05 00:00:00.000 2 Jossef Goldberg 71439 2014-05-22 00:00:00.000 2014-06-01 00:00:00.000 10 530 2014-06-05 00:00:00.000 3 Ken Sánchez 67605 2014-04-17 00:00:00.000 2014-04-27 00:00:00.000 10 512 2014-04-27 00:00:00.000 1 Ken Sánchez 67403 2014-04-15 00:00:00.000 2014-04-25 00:00:00.000 10 512 2014-04-27 00:00:00.000 2 Ken Sánchez 67302 2014-04-14 00:00:00.000 2014-04-24 00:00:00.000 10 512 2014-04-27 00:00:00.000 3 Michael Raheem 72158 2014-05-29 00:00:00.000 2014-06-08 00:00:00.000 10 448 2014-06-08 00:00:00.000 1 Michael Raheem 68758 2014-04-28 00:00:00.000 2014-05-08 00:00:00.000 10 448 2014-06-08 00:00:00.000 2 Michael Raheem 66662 2014-04-08 00:00:00.000 2014-04-18 00:00:00.000 10 448 2014-06-08 00:00:00.000 3 Michael Sullivan 72383 2014-05-31 00:00:00.000 2014-06-10 00:00:00.000 10 652 2014-06-10 00:00:00.000 1 Michael Sullivan 70886 2014-05-17 00:00:00.000 2014-05-27 00:00:00.000 10 652 2014-06-10 00:00:00.000 2 Michael Sullivan 67386 2014-04-15 00:00:00.000 2014-04-25 00:00:00.000 10 652 2014-06-10 00:00:00.000 3 Ovidiu Cracium 72366 2014-05-31 00:00:00.000 2014-06-10 00:00:00.000 10 593 2014-06-10 00:00:00.000 1 Ovidiu Cracium 72267 2014-05-30 00:00:00.000 2014-06-09 00:00:00.000 10 593 2014-06-10 00:00:00.000 2 Ovidiu Cracium 70869 2014-05-17 00:00:00.000 2014-05-28 00:00:00.000 11 593 2014-06-10 00:00:00.000 3 Rob Walters 72323 2014-05-31 00:00:00.000 2014-06-11 00:00:00.000 11 547 2014-06-11 00:00:00.000 1 Rob Walters 71422 2014-05-22 00:00:00.000 2014-06-01 00:00:00.000 10 547 2014-06-11 00:00:00.000 2 Rob Walters 70021 2014-05-09 00:00:00.000 2014-05-19 00:00:00.000 10 547 2014-06-11 00:00:00.000 3 Roberto Tamburello 70115 2014-05-10 00:00:00.000 2014-06-01 00:00:00.000 22 660 2014-06-01 00:00:00.000 1 Roberto Tamburello 69418 2014-05-04 00:00:00.000 2014-05-20 00:00:00.000 16 660 2014-06-01 00:00:00.000 2 Roberto Tamburello 67720 2014-04-18 00:0

___
___
___

# 6. `Product_Order_Analysis.sql`

## Proposition
This query analyzes product work orders in the AdventureWorks2019 database, calculating the total and average manufacturing duration for each product. It ranks the work orders by quantity, returning the top 5 orders per product.

## Tables Involved
- `Production.Product`: Stores product information, including `ProductID` and `Name`.
- `Production.WorkOrder`: Stores work order information, including `WorkOrderID`, `OrderQty`, `StartDate`, and `EndDate`.

### Further Details
- The `ProductOrderAnalysis` common table expression (CTE) calculates the manufacturing duration for each work order, along with total and average manufacturing duration per product using window functions.
- The `OrderRank` ranks work orders by `OrderQty` in descending order for each product.
- The main query selects the top 5 work orders for each product, sorted by `ProductName` and `OrderRank`.

In [27]:
USE	[AdventureWorks2019]
GO

WITH	ProductOrderAnalysis	AS	(
    SELECT
        p.ProductID,
        p.[Name]			AS	ProductName,
        woh.WorkOrderID,
        woh.OrderQty,
        woh.StartDate,
        woh.EndDate,
        DATEDIFF	(day,	woh.StartDate,	woh.EndDate)
							AS	ManufacturingDuration,
        SUM(woh.OrderQty)									OVER	(
			PARTITION	BY	p.ProductID
		)					AS	TotalOrderQuantity,
        AVG(DATEDIFF(day,	woh.StartDate,	woh.EndDate))	OVER	(
			PARTITION	BY	p.ProductID
		)					AS	AvgManufacturingDuration,
        RANK()	OVER	(
			PARTITION	BY	p.ProductID
				ORDER	BY	woh.OrderQty	DESC
		)					AS	OrderRank
    FROM
		Production.[Product]	p
    JOIN
		Production.WorkOrder	woh
			ON	p.ProductID	=	woh.ProductID
)

SELECT
    ProductName,
    WorkOrderID,
    OrderQty,
    ManufacturingDuration,
    TotalOrderQuantity,
    AvgManufacturingDuration,
    OrderRank
FROM
	ProductOrderAnalysis
WHERE
	OrderRank	<=	5
ORDER	BY
	ProductName,
	OrderRank;
GO

Commands completed successfully.

(1211 rows affected)

Total execution time: 00:00:00.049

ProductName WorkOrderID OrderQty ManufacturingDuration TotalOrderQuantity AvgManufacturingDuration OrderRank BB Ball Bearing 39424 39570 10 911890 10 1 BB Ball Bearing 42065 39270 10 911890 10 2 BB Ball Bearing 50530 34620 10 911890 10 3 BB Ball Bearing 17734 33420 10 911890 10 4 BB Ball Bearing 47660 33040 10 911890 10 5 Blade 39441 12062 10 236002 10 1 Blade 42082 11884 10 236002 10 2 Blade 17750 10288 10 236002 10 3 Blade 47677 9014 10 236002 10 4 Blade 50547 8984 10 236002 10 5 Chain Stays 39425 12062 10 234734 10 1 Chain Stays 42066 11884 10 234734 10 2 Chain Stays 17735 10110 10 234734 10 3 Chain Stays 47661 9014 10 234734 10 4 Chain Stays 50531 8984 10 234734 10 5 Down Tube 39426 6031 10 117367 10 1 Down Tube 42067 5942 10 117367 10 2 Down Tube 17736 5055 10 117367 10 3 Down Tube 47662 4507 10 117367 10 4 Down Tube 50532 4492 10 117367 10 5 Fork Crown 39443 6031 10 118001 10 1 Fork Crown 42084 5942 10 118001 10 2 Fork Crown 17752 5144 10 118001 10 3 Fork Crown 47679 4507 10 118001 10 4 Fork Crown 50549 4492 10 118001 10 5 Fork End 39442 12062 10 236002 10 1 Fork End 42083 11884 10 236002 10 2 Fork End 17751 10288 10 236002 10 3 Fork End 47678 9014 10 236002 10 4 Fork End 50548 8984 10 236002 10 5 Front Derailleur 39415 3864 16 91081 15 1 Front Derailleur 42056 3772 16 91081 15 2 Front Derailleur 17729 3342 16 91081 15 3 Front Derailleur 50521 3330 16 91081 15 4 Front Derailleur 47651 3244 16 91081 15 5 Handlebar Tube 39430 4245 10 94218 10 1 Handlebar Tube 42071 4158 10 94218 10 2 Handlebar Tube 17739 3695 10 94218 10 3 Handlebar Tube 50536 3518 10 94218 10 4 Handlebar Tube 47666 3375 10 94218 10 5 Head Tube 39431 6031 10 117367 10 1 Head Tube 42072 5942 10 117367 10 2 Head Tube 17740 5055 10 117367 10 3 Head Tube 47667 4507 10 117367 10 4 Head Tube 50537 4492 10 117367 10 5 HL Bottom Bracket 39423 884 16 23085 15 1 HL Bottom Bracket 5038 795 16 23085 15 2 HL Bottom Bracket 42064 793 16 23085 15 3 HL Bottom Bracket 13130 772 16 23085 15 4 HL Bottom Bracket 50529 719 16 23085 15 5 HL Crankset 5035 795 16 14568 15 1 HL Crankset 13127 772 16 14568 15 2 HL Crankset 9143 660 16 14568 15 3 HL Crankset 39420 613 16 14568 15 4 HL Crankset 42061 593 16 14568 15 5 HL Fork 42081 2425 16 48531 15 1 HL Fork 39440 2415 16 48531 15 2 HL Fork 69499 1946 16 48531 15 3 HL Fork 50546 1869 16 48531 15 4 HL Fork 47676 1836 16 48531 15 5 HL Headset 5019 795 16 14210 15 1 HL Headset 13111 772 16 14210 15 2 HL Headset 9127 660 16 14210 15 3 HL Headset 39356 613 16 14210 15 4 HL Headset 41997 593 16 14210 15 5 HL Hub 42074 5928 10 128226 10 1 HL Hub 39433 5866 10 128226 10 2 HL Hub 50539 5190 10 128226 10 3 HL Hub 69492 5002 10 128226 10 4 HL Hub 47669 4944 10 128226 10 5 HL Mountain Frame - Black, 38 39352 153 16 4318 15 1 HL Mountain Frame - Black, 38 41993 144 16 4318 15 2 HL Mountain Frame - Black, 38 22674 137 16 4318 15 3 HL Mountain Frame - Black, 38 47588 133 16 4318 15 4 HL Mountain Frame - Black, 38 17700 132 16 4318 15 5 HL Mountain Frame - Black, 42 22672 145 10 4479 10 1 HL Mountain Frame - Black, 42 19435 134 10 4479 10 2 HL Mountain Frame - Black, 42 17698 121 10 4479 10 3 HL Mountain Frame - Black, 42 32854 110 10 4479 10 4 HL Mountain Frame - Black, 42 50456 110 10 4479 10 4 HL Mountain Frame - Black, 44 5014 92 10 695 10 1 HL Mountain Frame - Black, 44 13106 78 10 695 10 2 HL Mountain Frame - Black, 44 1325 62 10 695 10 3 HL Mountain Frame - Black, 44 6318 61 10 695 10 4 HL Mountain Frame - Black, 44 9122 61 10 695 10 4 HL Mountain Frame - Black, 46 41992 87 10 2111 10 1 HL Mountain Frame - Black, 46 19436 86 10 2111 10 2 HL Mountain Frame - Black, 46 22673 81 10 2111 10 3 HL Mountain Frame - Black, 46 17699 81 10 2111 10 3 HL Mountain Frame - Black, 46 50457 74 10 2111 10 5 HL Mountain Frame - Black, 48 5015 77 10 747 10 1 HL Mountain Frame - Black, 48 13107 72 10 747 10 2 HL Mountain Frame - Black, 48 9123 72 10 747 10 2 HL Mountain Frame - Black, 48 14567 61 10 747 10 4 HL Mountain Frame - Black, 48 1326 59 10 747 10 5 HL M

___
___
___

# 7. `Employee_Production_Stats.sql`

## Proposition
The SQL script calculates and retrieves employee production statistics from the AdventureWorks2019 database. It uses a Common Table Expression (CTE) to calculate various metrics for each employee, including the total number of work orders, total quantity produced, and maximum work duration.

## Tables Involved
- `HumanResources.Employee`: Contains details of employees such as `BusinessEntityID`, which is used to link with other tables.
- `Production.WorkOrder`: Stores information about work orders, including `WorkOrderID`, `ProductID`, `OrderQty`, `StartDate`, and `EndDate`.
- `Production.Product`: Contains product details such as `ProductID` and `Name`.
- `Person.Person`: Stores personal information of individuals, including `FirstName`, `LastName`, and `BusinessEntityID`.

### Further Details
- Uses a Common Table Expression (CTE) named `EmployeeProductionStats` to organize the intermediate calculations.
- Calculates metrics such as `TotalWorkOrders`, `TotalQuantityProduced`, and `MaxWorkDuration` using window functions.


In [28]:
USE	[AdventureWorks2019]
GO

WITH	EmployeeProductionStats	AS	(
    SELECT
        e.BusinessEntityID										AS	EmployeeID,
        p.FirstName	+	' '	+	p.LastName						AS	EmployeeName,
        wor.WorkOrderID,
        wor.ProductID,
        pr.[Name]												AS	ProductName,
        wor.OrderQty,
        wor.StartDate,
        wor.EndDate,
        DATEDIFF	(day,	wor.StartDate,	wor.EndDate)	AS	WorkDuration,
        COUNT	(wor.WorkOrderID)								OVER	(
			PARTITION	BY	e.BusinessEntityID)				AS	TotalWorkOrders,
        SUM		(wor.OrderQty)									OVER	(
			PARTITION	BY	e.BusinessEntityID)				AS	TotalQuantityProduced,
        MAX		(DATEDIFF(day,	wor.StartDate,	wor.EndDate))	OVER	(
			PARTITION	BY	e.BusinessEntityID)				AS	MaxWorkDuration
    FROM
		HumanResources.Employee	e
    JOIN
		Production.WorkOrder	wor
			ON	e.BusinessEntityID	=	wor.ScrapReasonID
    JOIN
		Production.[Product]	pr
			ON	wor.ProductID		=	pr.ProductID
    JOIN
		Person.Person			p
			ON	e.BusinessEntityID	=	p.BusinessEntityID
)

SELECT
    EmployeeName,
    ProductName,
    WorkOrderID,
    OrderQty,
    WorkDuration,
    TotalWorkOrders,
    TotalQuantityProduced,
    MaxWorkDuration
FROM
	EmployeeProductionStats
ORDER	BY
	EmployeeName,
	ProductName,
	WorkOrderID;
GO

Commands completed successfully.

(729 rows affected)

Total execution time: 00:00:00.020

EmployeeName ProductName WorkOrderID OrderQty WorkDuration TotalWorkOrders TotalQuantityProduced MaxWorkDuration David Bradley BB Ball Bearing 496 40 10 51 31410 16 David Bradley BB Ball Bearing 2896 70 10 51 31410 16 David Bradley BB Ball Bearing 9796 40 10 51 31410 16 David Bradley BB Ball Bearing 13296 50 10 51 31410 16 David Bradley BB Ball Bearing 14296 50 10 51 31410 16 David Bradley BB Ball Bearing 19996 70 10 51 31410 16 David Bradley BB Ball Bearing 20296 90 10 51 31410 16 David Bradley BB Ball Bearing 26496 100 10 51 31410 16 David Bradley BB Ball Bearing 31796 180 10 51 31410 16 David Bradley BB Ball Bearing 34296 70 10 51 31410 16 David Bradley BB Ball Bearing 56296 280 10 51 31410 16 David Bradley Chain Stays 2595 2080 10 51 31410 16 David Bradley Chain Stays 51595 72 10 51 31410 16 David Bradley Fork Crown 57599 40 10 51 31410 16 David Bradley Fork Crown 63499 36 10 51 31410 16 David Bradley Fork End 47098 34 10 51 31410 16 David Bradley Fork End 48498 54 10 51 31410 16 David Bradley Fork End 57598 80 10 51 31410 16 David Bradley Fork End 63498 72 10 51 31410 16 David Bradley Fork End 63698 56 10 51 31410 16 David Bradley Fork End 67098 58 10 51 31410 16 David Bradley HL Hub 32898 3751 10 51 31410 16 David Bradley HL Hub 56398 44 10 51 31410 16 David Bradley HL Hub 67198 56 10 51 31410 16 David Bradley HL Hub 71098 58 10 51 31410 16 David Bradley HL Mountain Frame - Silver, 46 17697 137 10 51 31410 16 David Bradley HL Mountain Handlebars 41999 558 16 51 31410 16 David Bradley HL Road Frame - Black, 52 36699 37 10 51 31410 16 David Bradley HL Touring Frame - Blue, 60 50496 181 10 51 31410 16 David Bradley HL Touring Frame - Blue, 60 66096 156 10 51 31410 16 David Bradley LL Fork 69497 1581 16 51 31410 16 David Bradley LL Headset 53794 541 16 51 31410 16 David Bradley LL Mountain Seat Assembly 44695 319 16 51 31410 16 David Bradley LL Road Frame - Black, 58 6297 48 10 51 31410 16 David Bradley LL Road Frame - Black, 58 20997 107 10 51 31410 16 David Bradley ML Mountain Frame - Black, 40 27799 68 10 51 31410 16 David Bradley ML Mountain Frame - Black, 44 29398 54 10 51 31410 16 David Bradley ML Mountain Rear Wheel 27795 785 16 51 31410 16 David Bradley ML Road Frame - Red, 52 11696 46 10 51 31410 16 David Bradley ML Road Frame - Red, 52 13096 81 10 51 31410 16 David Bradley Road-250 Black, 44 32796 85 16 51 31410 16 David Bradley Seat Stays 44797 11632 10 51 31410 16 David Bradley Seat Stays 66997 164 10 51 31410 16 David Bradley Seat Stays 67397 108 10 51 31410 16 David Bradley Steerer 56898 3336 10 51 31410 16 David Bradley Steerer 61998 36 10 51 31410 16 David Bradley Steerer 62398 36 10 51 31410 16 David Bradley Top Tube 16095 3524 10 51 31410 16 David Bradley Touring-1000 Yellow, 46 50395 96 16 51 31410 16 David Bradley Touring-1000 Yellow, 46 65995 91 16 51 31410 16 David Bradley Touring-2000 Blue, 54 59697 72 16 51 31410 16 Diane Margheim Fork Crown 11749 943 10 37 43827 16 Diane Margheim Fork Crown 13149 2145 10 37 43827 16 Diane Margheim Fork Crown 50549 4492 10 37 43827 16 Diane Margheim Fork Crown 52849 34 10 37 43827 16 Diane Margheim Fork Crown 66149 4348 10 37 43827 16 Diane Margheim Fork Crown 70149 50 10 37 43827 16 Diane Margheim Fork End 11748 1886 10 37 43827 16 Diane Margheim Fork End 13148 4290 10 37 43827 16 Diane Margheim Fork End 49848 40 10 37 43827 16 Diane Margheim Fork End 50548 8984 10 37 43827 16 Diane Margheim Fork End 52848 68 10 37 43827 16 Diane Margheim Fork End 66148 8696 10 37 43827 16 Diane Margheim Fork End 70148 100 10 37 43827 16 Diane Margheim Head Tube 72050 42 10 37 43827 16 Diane Margheim HL Mountain Handlebars 7749 171 16 37 43827 16 Diane Margheim HL Road Front Wheel 19449 396 16 37 43827 16 Diane Margheim HL Touring Frame - Blue, 46 44749 70 10 37 43827 16 Diane Margheim HL Touring Seat Assembly 50447 548 16 37 43827 16 Diane Margheim HL Touring Seat Assembly 66047 426 16 37 43827 16 Diane Margheim LL Fork 17747 2008 16 37 43827 16 Diane Margheim LL Road Frame - Black,

___
___
___

# 8. `Product_Manufacturing_Performance.sql`

## Proposition
The SQL script calculates and retrieves product manufacturing performance statistics from the AdventureWorks2019 database. It uses a Common Table Expression (CTE) to calculate various metrics for each product, including the total quantity produced, average manufacturing duration, and ranking based on the quantity produced.

## Tables Involved
- `Production.Product`: Contains product details such as `ProductID` and `Name`.
- `Production.WorkOrder`: Stores information about work orders, including `WorkOrderID`, `ProductID`, `OrderQty`, `StartDate`, and `EndDate`.

### Further Details
- Uses a Common Table Expression (CTE) named `ProductPerformance` to organize the intermediate calculations.
- Calculates metrics such as `TotalProduced`, `AvgManufacturingDuration`, and `ProductionRank` using window functions.
- Filters the results to include only the top 3 work orders for each product based on `OrderQty`.

In [29]:
USE	[AdventureWorks2019]
GO

WITH	ProductPerformance	AS	(
    SELECT
        p.ProductID,
        p.[Name]		AS	ProductName,
        woh.WorkOrderID,
        woh.OrderQty,
        woh.StartDate,
        woh.EndDate,
        DATEDIFF
				(day,	woh.StartDate,	woh.EndDate)
						AS	ManufacturingDuration,
        SUM(woh.OrderQty)								OVER	(
				PARTITION	BY	p.ProductID
		)				AS	TotalProduced,
        AVG(DATEDIFF
				(day,	woh.StartDate,	woh.EndDate))	OVER	(
				PARTITION	BY	p.ProductID
		)				AS	AvgManufacturingDuration,
        RANK()											OVER	(
				PARTITION	BY	p.ProductID
					ORDER	BY	woh.OrderQty	DESC
		)				AS	ProductionRank
    FROM
		Production.[Product]	p
    JOIN
		Production.WorkOrder	woh
			ON	p.ProductID	=	woh.ProductID
)

SELECT
    ProductName,
    WorkOrderID,
    OrderQty,
    ManufacturingDuration,
    TotalProduced,
    AvgManufacturingDuration,
    ProductionRank
FROM
	ProductPerformance
WHERE
	ProductionRank	<=	3
ORDER	BY
	ProductName,
	ProductionRank;
GO

Commands completed successfully.

(734 rows affected)

Total execution time: 00:00:00.048

ProductName WorkOrderID OrderQty ManufacturingDuration TotalProduced AvgManufacturingDuration ProductionRank BB Ball Bearing 39424 39570 10 911890 10 1 BB Ball Bearing 42065 39270 10 911890 10 2 BB Ball Bearing 50530 34620 10 911890 10 3 Blade 39441 12062 10 236002 10 1 Blade 42082 11884 10 236002 10 2 Blade 17750 10288 10 236002 10 3 Chain Stays 39425 12062 10 234734 10 1 Chain Stays 42066 11884 10 234734 10 2 Chain Stays 17735 10110 10 234734 10 3 Down Tube 39426 6031 10 117367 10 1 Down Tube 42067 5942 10 117367 10 2 Down Tube 17736 5055 10 117367 10 3 Fork Crown 39443 6031 10 118001 10 1 Fork Crown 42084 5942 10 118001 10 2 Fork Crown 17752 5144 10 118001 10 3 Fork End 39442 12062 10 236002 10 1 Fork End 42083 11884 10 236002 10 2 Fork End 17751 10288 10 236002 10 3 Front Derailleur 39415 3864 16 91081 15 1 Front Derailleur 42056 3772 16 91081 15 2 Front Derailleur 17729 3342 16 91081 15 3 Handlebar Tube 39430 4245 10 94218 10 1 Handlebar Tube 42071 4158 10 94218 10 2 Handlebar Tube 17739 3695 10 94218 10 3 Head Tube 39431 6031 10 117367 10 1 Head Tube 42072 5942 10 117367 10 2 Head Tube 17740 5055 10 117367 10 3 HL Bottom Bracket 39423 884 16 23085 15 1 HL Bottom Bracket 5038 795 16 23085 15 2 HL Bottom Bracket 42064 793 16 23085 15 3 HL Crankset 5035 795 16 14568 15 1 HL Crankset 13127 772 16 14568 15 2 HL Crankset 9143 660 16 14568 15 3 HL Fork 42081 2425 16 48531 15 1 HL Fork 39440 2415 16 48531 15 2 HL Fork 69499 1946 16 48531 15 3 HL Headset 5019 795 16 14210 15 1 HL Headset 13111 772 16 14210 15 2 HL Headset 9127 660 16 14210 15 3 HL Hub 42074 5928 10 128226 10 1 HL Hub 39433 5866 10 128226 10 2 HL Hub 50539 5190 10 128226 10 3 HL Mountain Frame - Black, 38 39352 153 16 4318 15 1 HL Mountain Frame - Black, 38 41993 144 16 4318 15 2 HL Mountain Frame - Black, 38 22674 137 16 4318 15 3 HL Mountain Frame - Black, 42 22672 145 10 4479 10 1 HL Mountain Frame - Black, 42 19435 134 10 4479 10 2 HL Mountain Frame - Black, 42 17698 121 10 4479 10 3 HL Mountain Frame - Black, 44 5014 92 10 695 10 1 HL Mountain Frame - Black, 44 13106 78 10 695 10 2 HL Mountain Frame - Black, 44 1325 62 10 695 10 3 HL Mountain Frame - Black, 46 41992 87 10 2111 10 1 HL Mountain Frame - Black, 46 19436 86 10 2111 10 2 HL Mountain Frame - Black, 46 22673 81 10 2111 10 3 HL Mountain Frame - Black, 46 17699 81 10 2111 10 3 HL Mountain Frame - Black, 48 5015 77 10 747 10 1 HL Mountain Frame - Black, 48 13107 72 10 747 10 2 HL Mountain Frame - Black, 48 9123 72 10 747 10 2 HL Mountain Frame - Silver, 38 17701 112 16 4242 15 1 HL Mountain Frame - Silver, 38 19438 106 16 4242 15 2 HL Mountain Frame - Silver, 38 41994 98 16 4242 15 3 HL Mountain Frame - Silver, 42 17696 130 10 3174 10 1 HL Mountain Frame - Silver, 42 19433 113 10 3174 10 2 HL Mountain Frame - Silver, 42 22670 105 10 3174 10 3 HL Mountain Frame - Silver, 44 13103 83 10 601 10 1 HL Mountain Frame - Silver, 44 5011 66 10 601 10 2 HL Mountain Frame - Silver, 44 6315 60 10 601 10 3 HL Mountain Frame - Silver, 44 9119 60 10 601 10 3 HL Mountain Frame - Silver, 46 17697 137 10 2865 10 1 HL Mountain Frame - Silver, 46 19434 107 10 2865 10 2 HL Mountain Frame - Silver, 46 24252 106 10 2865 10 3 HL Mountain Frame - Silver, 48 5012 68 10 678 10 1 HL Mountain Frame - Silver, 48 13104 61 10 678 10 2 HL Mountain Frame - Silver, 48 6316 55 10 678 10 3 HL Mountain Front Wheel 5024 632 16 5173 15 1 HL Mountain Front Wheel 13116 590 16 5173 15 2 HL Mountain Front Wheel 9132 498 16 5173 15 3 HL Mountain Handlebars 17704 713 16 20047 15 1 HL Mountain Handlebars 19441 676 16 20047 15 2 HL Mountain Handlebars 22678 650 16 20047 15 3 HL Mountain Rear Wheel 5028 632 16 5801 15 1 HL Mountain Rear Wheel 13120 590 16 5801 15 2 HL Mountain Rear Wheel 9136 498 16 5801 15 3 HL Mountain Seat Assembly 17675 713 16 19547 15 1 HL Mountain Seat Assembly 19412 676 16 19547 15 2 HL Mountain Seat Assembly 22649 650 16 19547 15 3 HL Road Frame - Black, 44 17725 88 10 2101 10 1 HL Road Frame - Black, 44 32881 85 10 2101 10 2

___
___
___

# 9. `Sales_Performance_Analysis.sql`

## Proposition
The SQL script calculates and retrieves sales performance statistics from the AdventureWorks2019 database. It uses a Common Table Expression (CTE) to calculate various metrics for each salesperson, including the total sales, average order value, and ranking based on the total due amount.

## Tables Involved
- `Sales.SalesPerson`: Contains details of salespersons, including `BusinessEntityID`, which links with employee and person tables.
- `HumanResources.Employee`: Contains employee details such as `BusinessEntityID`, which is used to link with the salesperson and person tables.
- `Person.Person`: Stores personal information of individuals, including `FirstName`, `LastName`, and `BusinessEntityID`.
- `Sales.SalesOrderHeader`: Stores sales order information such as `SalesOrderID`, `TotalDue`, and `OrderDate`.

### Further Details
- Uses a Common Table Expression (CTE) named `SalesPerformance` to organize the intermediate calculations.
- Calculates metrics such as `TotalSales`, `AvgOrderValue`, and `OrderRank` using window functions.
- Filters the results to include only the top 5 sales orders for each salesperson based on `TotalDue`.

In [30]:
USE [AdventureWorks2019]
GO

WITH    SalesPerformance	AS	(
    SELECT
        sp.BusinessEntityID					AS	SalesPersonID,
        p.FirstName	+	' '	+	p.LastName	AS	SalesPersonName,
        soh.SalesOrderID,
        soh.TotalDue,
        soh.OrderDate,
        SUM(soh.TotalDue)	OVER	(
			PARTITION	BY	sp.BusinessEntityID
		)									AS	TotalSales,
        AVG(soh.TotalDue)	OVER	(
			PARTITION	BY	sp.BusinessEntityID
		)									AS	AvgOrderValue,
        ROW_NUMBER()		OVER	(
			PARTITION	BY	sp.BusinessEntityID
				ORDER	BY	soh.TotalDue	DESC
		)									AS	OrderRank
    FROM
		Sales.SalesPerson	sp
    JOIN
		HumanResources.Employee	e
			ON	sp.BusinessEntityID	=	e.BusinessEntityID
    JOIN
		Person.Person	p
			ON	e.BusinessEntityID	=	p.BusinessEntityID
    JOIN
		Sales.SalesOrderHeader	soh
			ON	sp.BusinessEntityID	=	soh.SalesPersonID
)

SELECT
    SalesPersonName,
    SalesOrderID,
    TotalDue,
    OrderDate,
    TotalSales,
    AvgOrderValue,
    OrderRank
FROM
	SalesPerformance
WHERE
	OrderRank	<=	5
ORDER	BY
	SalesPersonName,
	OrderRank;
GO

Commands completed successfully.

(85 rows affected)

Total execution time: 00:00:00.026

SalesPersonName SalesOrderID TotalDue OrderDate TotalSales AvgOrderValue OrderRank Amy Alberts 59064 81029.9462 2013-10-30 00:00:00.000 826417.4667 21190.1914 1 Amy Alberts 58908 80819.7335 2013-10-30 00:00:00.000 826417.4667 21190.1914 2 Amy Alberts 51837 77823.9958 2013-06-30 00:00:00.000 826417.4667 21190.1914 3 Amy Alberts 59044 71227.6778 2013-10-30 00:00:00.000 826417.4667 21190.1914 4 Amy Alberts 65201 60244.0493 2014-01-29 00:00:00.000 826417.4667 21190.1914 5 David Campbell 46643 123497.0664 2012-05-30 00:00:00.000 4207894.6025 22263.9926 1 David Campbell 51711 114536.7764 2013-06-30 00:00:00.000 4207894.6025 22263.9926 2 David Campbell 51123 105281.9588 2013-05-30 00:00:00.000 4207894.6025 22263.9926 3 David Campbell 44284 98932.197 2011-08-31 00:00:00.000 4207894.6025 22263.9926 4 David Campbell 47986 98786.051 2012-09-30 00:00:00.000 4207894.6025 22263.9926 5 Garrett Vargas 44534 96937.2022 2011-10-01 00:00:00.000 4069422.2109 17390.6932 1 Garrett Vargas 43890 84686.9878 2011-07-01 00:00:00.000 4069422.2109 17390.6932 2 Garrett Vargas 58932 80984.3252 2013-10-30 00:00:00.000 4069422.2109 17390.6932 3 Garrett Vargas 45553 77964.0532 2012-01-29 00:00:00.000 4069422.2109 17390.6932 4 Garrett Vargas 44547 77692.7415 2011-10-01 00:00:00.000 4069422.2109 17390.6932 5 Jae Pak 46616 170512.6689 2012-05-30 00:00:00.000 9585124.9477 27543.4624 1 Jae Pak 46607 135606.6769 2012-05-30 00:00:00.000 9585124.9477 27543.4624 2 Jae Pak 46645 114197.9702 2012-05-30 00:00:00.000 9585124.9477 27543.4624 3 Jae Pak 53535 111328.3281 2013-07-31 00:00:00.000 9585124.9477 27543.4624 4 Jae Pak 51160 111207.2228 2013-05-30 00:00:00.000 9585124.9477 27543.4624 5 Jillian Carson 46660 132727.8506 2012-05-30 00:00:00.000 11342385.8968 23979.6742 1 Jillian Carson 43884 130416.4829 2011-07-01 00:00:00.000 11342385.8968 23979.6742 2 Jillian Carson 44528 122500.6617 2011-10-01 00:00:00.000 11342385.8968 23979.6742 3 Jillian Carson 53506 119054.4623 2013-07-31 00:00:00.000 11342385.8968 23979.6742 4 Jillian Carson 47027 118290.7501 2012-06-30 00:00:00.000 11342385.8968 23979.6742 5 José Saraiva 53573 130249.2557 2013-07-31 00:00:00.000 6683536.6583 24662.4968 1 José Saraiva 47451 114753.0264 2012-07-31 00:00:00.000 6683536.6583 24662.4968 2 José Saraiva 51823 112685.2793 2013-06-30 00:00:00.000 6683536.6583 24662.4968 3 José Saraiva 45529 109340.8212 2012-01-29 00:00:00.000 6683536.6583 24662.4968 4 José Saraiva 53458 105420.9481 2013-07-31 00:00:00.000 6683536.6583 24662.4968 5 Linda Mitchell 47355 145741.8553 2012-07-31 00:00:00.000 11695019.0605 27978.5144 1 Linda Mitchell 51822 145454.366 2013-06-30 00:00:00.000 11695019.0605 27978.5144 2 Linda Mitchell 57186 126230.418 2013-09-30 00:00:00.000 11695019.0605 27978.5144 3 Linda Mitchell 51126 124397.7924 2013-05-30 00:00:00.000 11695019.0605 27978.5144 4 Linda Mitchell 57105 124249.4919 2013-09-30 00:00:00.000 11695019.0605 27978.5144 5 Lynn Tsoflias 53566 71729.8592 2013-07-31 00:00:00.000 1606441.4471 14737.9949 1 Lynn Tsoflias 51814 65741.4458 2013-06-30 00:00:00.000 1606441.4471 14737.9949 2 Lynn Tsoflias 71805 65263.2967 2014-05-01 00:00:00.000 1606441.4471 14737.9949 3 Lynn Tsoflias 65191 63426.4562 2014-01-29 00:00:00.000 1606441.4471 14737.9949 4 Lynn Tsoflias 57075 57438.3505 2013-09-30 00:00:00.000 1606441.4471 14737.9949 5 Michael Blythe 47395 165028.7482 2012-07-31 00:00:00.000 10475367.0751 23278.5935 1 Michael Blythe 53621 120512.2708 2013-07-31 00:00:00.000 10475367.0751 23278.5935 2 Michael Blythe 50289 118581.3375 2013-03-30 00:00:00.000 10475367.0751 23278.5935 3 Michael Blythe 47416 116463.9102 2012-07-31 00:00:00.000 10475367.0751 23278.5935 4 Michael Blythe 48336 113231.0188 2012-10-30 00:00:00.000 10475367.0751 23278.5935 5 Pamela Ansman-Wolfe 47033 105493.6317 2012-06-30 00:00:00.000 3748246.1218 39455.2223 1 Pamela Ansman-Wolfe 67297 103227.0017 2014-03-01 00:00:00.000 3748246.1218 39455.2223 2 Pamela Ansman-Wolfe 53518 99023.6736 2013-07-31 00:00:00.000 3748246.1218 39455.22

___
___
___

# 10. `Customer_High_Value_Orders.sql`

## Proposition
The SQL script calculates and retrieves high-value order information for customers from the AdventureWorks2019 database. It uses a Common Table Expression (CTE) to calculate various metrics for each customer, including the total amount spent and ranking based on the total due amount.

## Tables Involved
- `Sales.Customer`: Contains customer details such as `CustomerID` and links with the person table.
- `Person.Person`: Stores personal information of individuals, including `FirstName`, `LastName`, and `BusinessEntityID`.
- `Sales.SalesOrderHeader`: Stores sales order information such as `SalesOrderID`, `TotalDue`, and `OrderDate`.

### Further Details
- Uses a Common Table Expression (CTE) named `CustomerHighValueOrders` to organize the intermediate calculations.
- Calculates metrics such as `TotalSpent` and `OrderRank` using window functions.
- Filters the results to include only the top 2 orders for each customer based on `TotalDue` where the order amount is greater than 1000.

In [31]:
USE [AdventureWorks2019]
GO

WITH	CustomerHighValueOrders	AS	(
    SELECT
        c.CustomerID,
        p.FirstName	+	' '	+	p.LastName	AS	CustomerName,
        soh.SalesOrderID,
        soh.TotalDue,
        soh.OrderDate,
        SUM(soh.TotalDue)	OVER	(
			PARTITION	BY	c.CustomerID
		)	AS	TotalSpent,
        RANK()              OVER	(
			PARTITION	BY	c.CustomerID
				ORDER	BY	soh.TotalDue	DESC
		)	AS	OrderRank
    FROM
		Sales.Customer	c
    JOIN
		Person.Person	p
			ON	c.PersonID		=	p.BusinessEntityID
    JOIN
		Sales.SalesOrderHeader	soh
			ON	c.CustomerID	=	soh.CustomerID
    WHERE
		soh.TotalDue	>	1000
)

SELECT
    CustomerName,
    SalesOrderID,
    TotalDue,
    OrderDate,
    TotalSpent,
    OrderRank
FROM
	CustomerHighValueOrders
WHERE
	OrderRank	<=	2
ORDER	BY
	CustomerName,
	OrderRank;
GO


Commands completed successfully.

(11744 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.105

CustomerName SalesOrderID TotalDue OrderDate TotalSpent OrderRank A. Leonetti 53489 1814.1819 2013-07-31 00:00:00.000 1814.1819 1 Aaron Allen 46413 3756.989 2012-05-03 00:00:00.000 3756.989 1 Aaron Baker 66073 1934.8329 2014-02-09 00:00:00.000 1934.8329 1 Aaron Campbell 66146 1276.8054 2014-02-10 00:00:00.000 1276.8054 1 Aaron Collins 43821 3953.9884 2011-06-27 00:00:00.000 6682.2887 1 Aaron Collins 70925 2728.3003 2014-04-18 00:00:00.000 6682.2887 2 Aaron Con 46054 9619.3538 2012-03-30 00:00:00.000 46535.4204 1 Aaron Con 45297 7246.2473 2012-01-01 00:00:00.000 46535.4204 2 Aaron Diaz 44813 3953.9884 2011-11-01 00:00:00.000 6662.6749 1 Aaron Diaz 55025 2708.6865 2013-08-25 00:00:00.000 6662.6749 2 Aaron Evans 59968 2688.5092 2013-11-11 00:00:00.000 2688.5092 1 Aaron Foster 72567 2742.6432 2014-05-09 00:00:00.000 5428.2794 1 Aaron Foster 61714 2685.6362 2013-12-07 00:00:00.000 5428.2794 2 Aaron Gonzales 73248 2000.5583 2014-05-18 00:00:00.000 2000.5583 1 Aaron Hayes 67240 2574.6279 2014-02-28 00:00:00.000 2574.6279 1 Aaron Hughes 65550 2659.7792 2014-02-01 00:00:00.000 4924.0328 1 Aaron Hughes 48933 2264.2536 2012-12-16 00:00:00.000 4924.0328 2 Aaron King 56329 2649.8453 2013-09-16 00:00:00.000 5257.6232 1 Aaron King 51443 2607.7779 2013-06-15 00:00:00.000 5257.6232 2 Aaron Kumar 50363 2264.2536 2013-04-02 00:00:00.000 2264.2536 1 Aaron Lal 70144 2552.5169 2014-04-07 00:00:00.000 2552.5169 1 Aaron Li 63403 2637.8671 2014-01-01 00:00:00.000 2637.8671 1 Aaron Nelson 48679 2288.9187 2012-11-24 00:00:00.000 2288.9187 1 Aaron Patterson 60694 1308.8283 2013-11-22 00:00:00.000 1308.8283 1 Aaron Ross 54648 2626.5408 2013-08-18 00:00:00.000 2626.5408 1 Aaron Russell 72839 1297.8004 2014-05-13 00:00:00.000 1297.8004 1 Aaron Scott 62510 2754.0136 2013-12-20 00:00:00.000 2754.0136 1 Aaron Wang 46162 3953.9884 2012-04-06 00:00:00.000 6568.9267 1 Aaron Wang 53859 2614.9383 2013-08-04 00:00:00.000 6568.9267 2 Aaron Wright 45861 3953.9884 2012-03-07 00:00:00.000 11949.0613 1 Aaron Wright 60850 2699.9018 2013-11-25 00:00:00.000 11949.0613 2 Aaron Young 46213 3953.9884 2012-04-13 00:00:00.000 6656.2217 1 Aaron Young 52360 2702.2333 2013-07-09 00:00:00.000 6656.2217 2 Abby Arthur 45616 3953.9884 2012-02-03 00:00:00.000 3953.9884 1 Abby Garcia 59810 1429.1297 2013-11-09 00:00:00.000 1429.1297 1 Abby Patel 51009 2288.9187 2013-05-22 00:00:00.000 4207.1766 1 Abby Patel 72485 1918.2579 2014-05-08 00:00:00.000 4207.1766 2 Abby Raman 65610 2570.1858 2014-02-02 00:00:00.000 4859.1045 1 Abby Raman 50008 2288.9187 2013-03-11 00:00:00.000 4859.1045 2 Abby Sai 44475 3756.989 2011-09-29 00:00:00.000 9130.0847 1 Abby Sai 51668 2696.189 2013-06-28 00:00:00.000 9130.0847 2 Abby Sanchez 45753 3953.9884 2012-02-23 00:00:00.000 6653.8902 1 Abby Sanchez 59692 2699.9018 2013-11-07 00:00:00.000 6653.8902 2 Abby Sandberg 45078 3953.9884 2011-12-01 00:00:00.000 6572.7942 1 Abby Sandberg 68900 2618.8058 2014-03-24 00:00:00.000 6572.7942 2 Abby Subram 73938 2688.5092 2014-05-27 00:00:00.000 7596.2337 1 Abby Subram 55969 2618.8058 2013-09-10 00:00:00.000 7596.2337 2 Abe Tramel 45806 3292.9062 2012-02-29 00:00:00.000 6374.9253 1 Abe Tramel 43685 3082.0191 2011-05-31 00:00:00.000 6374.9253 2 Abigail Bailey 50916 2288.9187 2013-05-14 00:00:00.000 2288.9187 1 Abigail Brooks 45923 3953.9884 2012-03-16 00:00:00.000 6517.5774 1 Abigail Brooks 60361 2563.589 2013-11-17 00:00:00.000 6517.5774 2 Abigail Butler 59571 1966.3144 2013-11-05 00:00:00.000 1966.3144 1 Abigail Clark 46445 3953.9884 2012-05-08 00:00:00.000 6534.1303 1 Abigail Clark 64655 2580.1419 2014-01-20 00:00:00.000 6534.1303 2 Abigail Coleman 68076 1238.1415 2014-03-11 00:00:00.000 1238.1415 1 Abigail Coleman 46240 3953.9884 2012-04-16 00:00:00.000 5336.476 1 Abigail Coleman 69011 1382.4876 2014-03-25 00:00:00.000 5336.476 2 Abigail Cox 68533 1272.6948 2014-03-18 00:00:00.000 1272.6948 1 Abigail Diaz 73233 2618.8169 2014-05-18 00:00:00.000 2618.8169 1 Abigail Foster 46133 3953.9884 2012-04-02 00:00:00.000 6622.5524 1 